# Vision probaliste

In [44]:
import numpy as np
import matplotlib.pyplot as plt
import networkx as nx
import random
from matplotlib.animation import FuncAnimation
from matplotlib.colors import LinearSegmentedColormap
from matplotlib.cm import ScalarMappable
from IPython.display import HTML

In [83]:
reseau1_Influence = np.array([[0, 0.25, 0.75, 0],
                              [0.25, 0, 0, 0.75],
                              [0, 0, 1, 0],
                              [0, 0, 0, 1]])
reseau1_Opinion = [1.0, 0.75, 0.25, 0] #L'indice correpond au noeud dans le graphe
reseau1_Pos = {
    0: (0, 0),    # Position du nœud 0
    1: (1, 0),    # Position du nœud 1
    2: (0, 1),   # Position du nœud 2
    3: (1, 1)     # Position du nœud 3
}

#Traduction pour affichage car DiGraph n'accepte que des matrices composées de 0 ou de 1
def tradReseauAffichage(reseau: np.array):
    tradReseau = reseau.copy()
    for noeud in tradReseau:
        for influence in noeud:
            if influence != 0: #Si il y a une influence alors il y a une connection
                influence = 1
    return tradReseau

#Affichage graphe
def generateColorGradientMap(opinion):
    # # colors = ['red', 'lightgrey', 'blue']  # Mapping 0 to red, 0.5 to lightgrey, and 1 to blue
    # # cm = LinearSegmentedColormap.from_list('custom_cmap', colors)
    # # node_colors = [cm(value) for value in opinion]
    # node_colors = [plt.cm.coolwarm(1 - value) for value in opinion]
    # return node_colors
    colors = ['red', 'lightgrey', 'blue']
    n_bins = 100 
    cm = LinearSegmentedColormap.from_list('custom_cmap', colors, N=n_bins)
    node_colors = [cm(value) for value in opinion] 
    return node_colors, cm 

def generateGraph(reseau_Influence, reseau_Opinion, desiredPos, ax, cm):
    G = nx.DiGraph()
    n = reseau_Influence.shape[0]
    for i in range(len(reseau_Opinion)):
        G.add_node(i, value=reseau_Opinion[i])
    for i in range(n):
        for j in range(n):
            if reseau_Influence[i, j] > 0:  # Si il y a une connexion
                G.add_edge(i, j, weight=reseau_Influence[i, j])  # Ajouter les arcs avec le poids
    edges = G.edges(data=True)  # Récupération des arcs avec poids
    weights = [edge[2]['weight'] for edge in edges]  # Création d'une liste contenant que les poids

    # Normalisation des poids pour l'épaisseur des arcs
    min_weight = min(weights)
    max_weight = max(weights)
    normalized_weights = [(weight - min_weight) / (max_weight - min_weight) * 2 + 1 for weight in weights]

    # Dessin des nœuds et arcs
    node_colors, _ = generateColorGradientMap(reseau_Opinion)
    nx.draw(G, pos=desiredPos, node_color=node_colors, with_labels=True, ax=ax, node_size=700)
    edge_labels = {(u, v): f'{d["weight"]:.2f}' for u, v, d in edges} #Valeur des arcs (donc les poids d'influence)
    nx.draw_networkx_edge_labels(G, desiredPos, edge_labels=edge_labels, ax=ax)
    nx.draw_networkx_edges(G, pos=desiredPos, edgelist=edges, width=normalized_weights, ax=ax)

#Vérifications de la matrice avant de pourvoir faire des calculs dessus
def verifMatConforme(mat, opinions):
    if len(mat) != len(opinions):
        raise Exception("La matrice n'as pas assez de points pour correspondre au nombre de noeud des opinions")
    for noeud in mat:
        if len(noeud) != len(opinions):
            raise Exception("La ligne matrice n'as pas assez de points pour correspondre au nombre de noeud des opinions")
        sommeInfluence = 0
        for influence in noeud:
            sommeInfluence += influence
        if sommeInfluence != 1:
            raise Exception("La somme des influence de la  matrice n'est pas égale à 1")

#Mise à jour des opinions
def newOpinion(x:int, matProbaMarkov, opinions):
    # print(matProbaMarkov, opinions)
    influenceNode = {}
    for y in range( len(matProbaMarkov[x]) ):
        influenceNode[matProbaMarkov[x][y]] = y
    influenceNodeWithoutZeroSort = {k: v for k, v in influenceNode.items() if k != 0.0}
    #print(influenceNodeWithoutZeroSort)

    # for v, k in influenceNodeWithoutZeroSort.items():
    #     print(v, k, v * opinions[k])
    
    esperance = sum(v * opinions[k] for v, k in influenceNodeWithoutZeroSort.items())
    #print("res",esperance)
    return esperance

def createMarkovMat(initialOpinions, influenceMatrix, nbIteration=1000):  
    matMarkov = [[0]*len(influenceMatrix[0])]*len(influenceMatrix)
    
    for l in range(len(influenceMatrix)): #Pour chaque ligne (noeud)
        currentProbaList = [0]*len(influenceMatrix)
        influenceNode = {}
        for y in range( len(influenceMatrix[l]) ):
            influenceNode[influenceMatrix[l][y]] = y
        influenceNodeWithoutZeroSort = {k: v for k, v in influenceNode.items() if k != 0.0}
        for m in range(nbIteration): #Je fais 100x
            proba = random.random() # Valeur entre 0 et 1
            previous = 0
            for v, k in influenceNodeWithoutZeroSort.items(): #Pour chaque noeud qui ont une influence    
                if previous <= proba and proba <= previous + v: #Quand je trouve le chemin a prendre
                    currentProbaList[k] += 1 # Alors je l'incrémente d'un passage
                    break;
                else:
                    previous += v #Sinon je met a jour la prochaine borne pour la comparaison
        matMarkov[l] = [prob/nbIteration for prob in currentProbaList] #Une fois que j'ai calculé le nombre de passage j'affecte la liste de proba
    return matMarkov #Je renvoie la matrice de proba

def calcNextOpinionStep(matProbaMarkov, listOpinions):
    #verifMatConforme(matProbaMarkov, listOpinions)
    # print("matProbaMarkov", matProbaMarkov)
    # print("listOpinions", listOpinions)
    nextListOpinions = []
    for i in range(len(listOpinions)):
        nextListOpinions.append(newOpinion(i, matProbaMarkov, listOpinions))
    # print("nextListOpinions", nextListOpinions)
    return nextListOpinions

def createAnimation(nbGeneration, initialOpinions, influenceMatrix, positions, isProbabilistMode=False):
    opinions_list = [initialOpinions]
    matProbaMarkov = createMarkovMat(initialOpinions, influenceMatrix)
    for _ in range(nbGeneration):
        initialOpinions = calcNextOpinionStep(matProbaMarkov, initialOpinions)
        opinions_list.append(initialOpinions)
    fig, ax = plt.subplots()

    _, cm = generateColorGradientMap(opinions_list[0])
    sm = ScalarMappable(cmap=cm, norm=plt.Normalize(vmin=0, vmax=1))
    
    def update(frame):
        ax.clear()
        generateGraph(influenceMatrix, opinions_list[frame], positions, ax, cm)
        ax.set_title(f'Étape {frame}')

    cbar = fig.colorbar(sm, ax=ax, orientation='vertical')
    cbar.set_label('Niveau d\'opinion')
    
    ani = FuncAnimation(fig, update, frames=len(opinions_list), interval=1000, repeat=False)
    plt.close(fig)  # Close the figure to avoid display before returning

    return ani
    
HTML(createAnimation(4, reseau1_Opinion, reseau1_Influence, reseau1_Pos).to_jshtml())

matProbaMarkov [[0.0, 0.265, 0.735, 0.0], [0.221, 0.0, 0.0, 0.779], [0.0, 0.0, 1.0, 0.0], [0.0, 0.0, 0.0, 1.0]]
listOpinions [1.0, 0.75, 0.25, 0]
nextListOpinions [0.3825, 0.221, 0.25, 0.0]
matProbaMarkov [[0.0, 0.265, 0.735, 0.0], [0.221, 0.0, 0.0, 0.779], [0.0, 0.0, 1.0, 0.0], [0.0, 0.0, 0.0, 1.0]]
listOpinions [0.3825, 0.221, 0.25, 0.0]
nextListOpinions [0.242315, 0.0845325, 0.25, 0.0]
matProbaMarkov [[0.0, 0.265, 0.735, 0.0], [0.221, 0.0, 0.0, 0.779], [0.0, 0.0, 1.0, 0.0], [0.0, 0.0, 0.0, 1.0]]
listOpinions [0.242315, 0.0845325, 0.25, 0.0]
nextListOpinions [0.2061511125, 0.053551615000000004, 0.25, 0.0]
matProbaMarkov [[0.0, 0.265, 0.735, 0.0], [0.221, 0.0, 0.0, 0.779], [0.0, 0.0, 1.0, 0.0], [0.0, 0.0, 0.0, 1.0]]
listOpinions [0.2061511125, 0.053551615000000004, 0.25, 0.0]
nextListOpinions [0.197941177975, 0.045559395862500005, 0.25, 0.0]


In [81]:
reseau6_Influence = np.array([[0, 1/2, 1/2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
                              [1/4, 0, 0, 1/4, 1/4, 1/4, 0, 0, 0, 0, 0, 0, 0, 0, 0],
                              [1/4, 0, 0, 0, 0, 0, 1/4, 1/4, 1/4, 0, 0, 0, 0, 0, 0],
                              [0, 1/3, 0, 0, 0, 0, 0, 0, 0, 1/3, 1/3, 0, 0, 0, 0],
                              [0, 1/2, 0, 0, 0, 0, 0, 0, 0, 0, 1/2, 0, 0, 0, 0],
                              [0, 1/3, 0, 0, 0, 0, 0, 0, 0, 0, 1/3, 1/3, 0, 0, 0],
                              [0, 0, 1/3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1/3, 1/3, 0],
                              [0, 0, 1/2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1/2, 0],
                              [0, 0, 1/3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1/3, 1/3],
                              [0, 0, 0, 1/2, 0, 0, 0, 0, 0, 0, 1/2, 0, 0, 0, 0],
                              [0, 0, 0, 1/5, 1/5, 1/5, 0, 0, 0, 1/5, 0, 1/5, 0, 0, 0],
                              [0, 0, 0, 0, 0, 1/2, 0, 0, 0, 0, 1/2, 0, 0, 0, 0],
                              [0, 0, 0, 0, 0, 0, 1/2, 0, 0, 0, 0, 0, 0, 1/2, 0],
                              [0, 0, 0, 0, 0, 0, 1/5, 1/5, 1/5, 0, 0, 0, 1/5, 0, 1/5],
                              [0, 0, 0, 0, 0, 0, 0, 0, 1/2, 0, 0, 0, 0, 1/2, 0]])
reseau6_Opinion = [0.5, 0.65, 0.5, 0.75, 0.75, 0.75, 0.5, 0.5, 0.5, 1.0, 1.0, 1.0, 0.5, 0.5, 0.5] #L'indice correpond au noeud dans le graphe
reseau6_Pos = {
    0: (3, 3),    # Position du nœud 0
    1: (1, 2),    # Position du nœud 1
    2: (5, 2),    # Position du nœud 2
    3: (0, 1),    # Position du nœud 3
    4: (1, 1),    # Position du nœud 3
    5: (2, 1),
    6: (4, 1),
    7: (5, 1),
    8: (6, 1),
    9: (0, 0),
    10: (1, 0),
    11: (2, 0),
    12: (4, 0),
    13: (5, 0),
    14: (6, 0),
}

HTML(createAnimation(50, reseau6_Opinion, reseau6_Influence, reseau6_Pos).to_jshtml())

[0.2415, 0.186, 0.1075, 0.341, 0.507, 0.341, 0.1615, 0.2565, 0.183, 0.487, 0.201, 0.49, 0.257, 0.09, 0.252]
[0.051922499999999996, 0.084568, 0.039345, 0.068541, 0.10190700000000001, 0.16709000000000002, 0.02907, 0.04617, 0.092232, 0.097887, 0.09849000000000001, 0.09849000000000001, 0.04626, 0.04536, 0.04536]
[0.019003634999999998, 0.04143832, 0.019829879999999998, 0.033585090000000005, 0.04993443, 0.033585090000000005, 0.01465128, 0.02326968, 0.01660176, 0.04796463, 0.019796490000000003, 0.0482601, 0.02331504, 0.0081648, 0.02286144]
[0.009577832039999998, 0.008329102320000002, 0.0035693784, 0.006750603090000001, 0.010036820430000001, 0.016456694100000002, 0.0026372304, 0.0041885424, 0.00836728704, 0.009640890630000001, 0.0097002801, 0.009700280100000002, 0.0041967072, 0.0041150592, 0.0041150592]
[0.0017240097672, 0.004081260136800001, 0.0017989667135999998, 0.0033077955141, 0.0049180420107, 0.003307795514100001, 0.0013291641216000001, 0.0021110253696000002, 0.0015061116672, 0.004724036

In [64]:
reseau4_Influence = np.array([[0, 0.33, 0, 0, 0, 0, 0, 0.33, 0.34],
                              [0.33, 0, 0.33, 0, 0, 0, 0, 0, 0.34],
                              [0, 0.33, 0, 0.33, 0, 0, 0, 0, 0.34],
                              [0, 0, 0.33, 0, 0.33, 0, 0, 0, 0.34],
                              [0, 0, 0, 0.33, 0, 0.33, 0, 0, 0.34],
                              [0, 0, 0, 0, 0.33, 0, 0.33, 0, 0.34],
                              [0, 0, 0, 0, 0, 0.33, 0, 0.33, 0.34],
                              [0.33, 0, 0, 0, 0, 0, 0.33, 0, 0.34],
                              [0.5, 0, 0, 0, 0, 0, 0, 0, 0.5]])
reseau4_Opinion = [1.0, 0.9, 0.8, 0.7, 0.6, 0.5, 0.4, 0.3, 0.2] #L'indice correpond au noeud dans le graphe
reseau4_Pos = {
    0: (0, 1),    # Position du nœud 0
    1: (0, 3),    # Position du nœud 1
    2: (1, 4),    # Position du nœud 2
    3: (3, 4),    # Position du nœud 3
    4: (4, 3),    # Position du nœud 3
    5: (4, 1),
    6: (3, 0),
    7: (1, 0),
    8: (2, 2)
}

HTML(createAnimation(4, reseau4_Opinion, reseau4_Influence, reseau4_Pos).to_jshtml())

C:\Users\Mikado\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\networkx\drawing\nx_pylab.py:457: UserWarning: No data for colormapping provided via 'c'. Parameters 'cmap' will be ignored
  node_collection = ax.scatter(
